In [2]:
import os
import time
import random

import gym 
import optuna
from FurutaPendulum import FurutaPendulum
from wrappers import StepTimeCtrl, HistoryWrapper

from stable_baselines3 import SAC
from stable_baselines3 import PPO
from stable_baselines3 import TD3
from stable_baselines3.common.vec_env import VecFrameStack
from stable_baselines3.common.evaluation import evaluate_policy

In [3]:
MAX_STEP_TIME = 1/60 #s
env = HistoryWrapper(StepTimeCtrl(FurutaPendulum(1000, MAX_STEP_TIME)),alpha=1e0)

In [ ]:
env.uC.read_state()

In [ ]:
env.update_state()
env.get_obs()

In [ ]:
from stable_baselines3.common.env_checker import check_env
check_env(env, warn=True)

In [ ]:
def optimize_sac(trial):
    # Define the hyperparameters to optimize
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-2)
    train_freq = trial.suggest_int('train_freq', 1, 10)
    target_entropy = trial.suggest_float('target_entropy', -5, 5)
    sde_sample_freq = trial.suggest_float('sde_sample_freq', 10, 70)

    # Create the environment
    MAX_STEP_TIME = 1/60 #s
    env = HistoryWrapper(StepTimeCtrl(FurutaPendulum(1000, MAX_STEP_TIME)))
    # Create the SAC agent
    model = SAC("MlpPolicy", env, use_sde=True, sde_sample_freq=sde_sample_freq, 
                learning_rate=learning_rate,
                target_entropy=target_entropy, learning_starts=500,
                train_freq=(train_freq, "episode"))
    # Train the agent
    model.learn(total_timesteps=5000)
    env.close()
    time.sleep(60 * 5)
    # Get the final reward
    return model.get_average_reward()

study = optuna.create_study(direction='maximize')
study.optimize(optimize_sac, n_trials=100)

print(study.best_params)

In [ ]:
env.close()


In [ ]:
env.reset()

In [5]:
log_path = os.path.join('Training', 'Logs')
model = SAC("MlpPolicy", env, verbose=1, tensorboard_log=log_path, use_sde=True, sde_sample_freq=64)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [ ]:
log_path = os.path.join('Training', 'Logs')
model = TD3("MlpPolicy", env, verbose=1, tensorboard_log=log_path)

In [ ]:
log_path = os.path.join('Training', 'Logs')
model = PPO("MlpPolicy", env, verbose=1, tensorboard_log=log_path, use_sde=True, sde_sample_freq=128)

In [ ]:
model_path = os.path.join('Training', 'Models','SAC_280K')
model = SAC.load(model_path, env)

In [6]:
for i in range(0,20):
    model.learn(total_timesteps=20000)
    model_path = os.path.join('Training', 'Models','SAC_20k'+ '_' + str(i))
    model.save(model_path)
    env.uC.reset()
    time.sleep(60 * 3)

Logging to Training\Logs\SAC_1


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 270       |
|    ep_rew_mean     | -3.45e+03 |
| time/              |           |
|    episodes        | 4         |
|    fps             | 10        |
|    time_elapsed    | 100       |
|    total_timesteps | 1079      |
| train/             |           |
|    actor_loss      | 47.5      |
|    critic_loss     | 49.4      |
|    ent_coef        | 0.888     |
|    ent_coef_loss   | -0.112    |
|    learning_rate   | 0.0003    |
|    n_updates       | 978       |
|    std             | 0.0501    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 151       |
|    ep_rew_mean     | -2.45e+03 |
| time/              |           |
|    episodes        | 8         |
|    fps             | 9         |
|    time_elapsed    | 124       |
|    total_timesteps | 1210      |
| train/             |           |
|    actor_loss      | 57        |
|    critic_loss     | 6.9e+03   |
|    ent_coef        | 0.872     |
|    ent_coef_loss   | 0.0855    |
|    learning_rate   | 0.0003    |
|    n_updates       | 1109      |
|    std             | 0.0501    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 128       |
|    ep_rew_mean     | -2.19e+03 |
| time/              |           |
|    episodes        | 12        |
|    fps             | 9         |
|    time_elapsed    | 162       |
|    total_timesteps | 1540      |
| train/             |           |
|    actor_loss      | 79.7      |
|    critic_loss     | 2.64e+03  |
|    ent_coef        | 0.865     |
|    ent_coef_loss   | 0.0602    |
|    learning_rate   | 0.0003    |
|    n_updates       | 1439      |
|    std             | 0.0499    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 108       |
|    ep_rew_mean     | -2.09e+03 |
| time/              |           |
|    episodes        | 16        |
|    fps             | 9         |
|    time_elapsed    | 189       |
|    total_timesteps | 1728      |
| train/             |           |
|    actor_loss      | 92.6      |
|    critic_loss     | 1.26e+04  |
|    ent_coef        | 0.873     |
|    ent_coef_loss   | 0.106     |
|    learning_rate   | 0.0003    |
|    n_updates       | 1627      |
|    std             | 0.0499    |
----------------------------------


...

----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1e+03     |
|    ep_rew_mean     | -8.87e+03 |
| time/              |           |
|    episodes        | 4         |
|    fps             | 13        |
|    time_elapsed    | 305       |
|    total_timesteps | 4000      |
| train/             |           |
|    actor_loss      | 952       |
|    critic_loss     | 94        |
|    ent_coef        | 0.578     |
|    ent_coef_loss   | -0.863    |
|    learning_rate   | 0.0003    |
|    n_updates       | 63599     |
|    std             | 0.0569    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1e+03     |
|    ep_rew_mean     | -8.68e+03 |
| time/              |           |
|    episodes        | 8         |
|    fps             | 12        |
|    time_elapsed    | 628       |
|    total_timesteps | 8000      |
| train/             |           |
|    actor_loss      | 956       |
|    critic_loss     | 51.1      |
|    ent_coef        | 0.51      |
|    ent_coef_loss   | -0.692    |
|    learning_rate   | 0.0003    |
|    n_updates       | 67599     |
|    std             | 0.0582    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1e+03     |
|    ep_rew_mean     | -8.42e+03 |
| time/              |           |
|    episodes        | 12        |
|    fps             | 12        |
|    time_elapsed    | 949       |
|    total_timesteps | 12000     |
| train/             |           |
|    actor_loss      | 954       |
|    critic_loss     | 121       |
|    ent_coef        | 0.493     |
|    ent_coef_loss   | -0.384    |
|    learning_rate   | 0.0003    |
|    n_updates       | 71599     |
|    std             | 0.0592    |
----------------------------------


----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1e+03     |
|    ep_rew_mean     | -8.21e+03 |
| time/              |           |
|    episodes        | 16        |
|    fps             | 12        |
|    time_elapsed    | 1282      |
|    total_timesteps | 16000     |
| train/             |           |
|    actor_loss      | 956       |
|    critic_loss     | 174       |
|    ent_coef        | 0.467     |
|    ent_coef_loss   | 0.0625    |
|    learning_rate   | 0.0003    |
|    n_updates       | 75599     |
|    std             | 0.0598    |
----------------------------------


KeyboardInterrupt: 

In [ ]:
episodes = 20
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0 
    
    while not done:
        action = env.action_space.sample()
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))
env.close()

In [ ]:
env.observation_space.shape

In [ ]:
evaluate_policy(model, env, n_eval_episodes=10, render=False)

In [ ]:
obs = env.reset()
while True:
    action, _states = model.predict(obs)
    obs, rewards, done, info = env.step(action)
    if done is True:
        obs = env.reset()

# 8. View logs

In [ ]:
log_path = os.path.join('Training', 'Logs')
training_log_path = os.path.join(log_path,)
!tensorboard --logdir={training_log_path} --host localhost --port 8088